In [1]:
import os
import time
import functions
import numpy as np
import pandas as pd
from functools import reduce
from datetime import datetime
from pyspark.sql import Window
from pyspark.sql.types import *
import matplotlib.pyplot as plt
from pyspark.sql.functions import *
from pyspark.sql import SparkSession, Row
from pyspark.ml.feature import StandardScaler, VectorAssembler
#from pyspark.sql.functions import col, create_map, lit
from itertools import chain

%matplotlib inline

# Initialize Spark

We will create our Spark program using **SparkSession** ...

In [2]:
appName = "my-tfm"

ss = SparkSession.builder.appName(appName).config("spark.some.config.option", "4g").getOrCreate()
print(ss)
sc = ss.sparkContext
print(sc)

<SparkContext master=yarn appName=my-tfm>


In [234]:
ss.stop()

# Build the dataset

We will load all the data, replace missing values and join all the datasets so that we can work with a single dataset with 60 columns in which each patient has the rows of its corresponding dataset.

* **Historical data:** http://archive.ics.uci.edu/ml/datasets/Diabetes+130-US+hospitals+for+years+1999-2008
* **Prediction data:** https://www.kaggle.com/kumargh/pimaindiansdiabetescsv
* **Analysis (time-series):** http://archive.ics.uci.edu/ml/datasets/Diabetes

### Load the files

* The first dataset, *historical data* has 101.766 rows and ---- columns. 
* The second dataset, *prediction data* has 768 rows and --- columns.
* The third dataset, *analysis (time-series)* has 70 patients with around 500 rows each and 4 variables.

In [213]:
# Load first dataset (historical data)
# hist_data = functions.load_data(ss, "diabetic_data.csv")

# Load second dataset (prediction data)
# col_names = ['Pregnancies', 'Glucose', 'BloodPressure', 'SkinThickness',\
#              'Insulin', 'BMI', 'DiabetesPedigreeFunction', 'Age', 'Class']
# pred_data = functions.load_data(ss, "pima-indians-diabetes.csv", hdr=False, col_names=col_names)

# # Load third dataset (analysis data)
an_data = functions.load_ts(sc, 70, 'data')

29-07-2020 23:20:59 - Loading data-01 file....
Loaded 943 rows and 5 columns
29-07-2020 23:21:00 - Loading data-02 file....
Loaded 761 rows and 5 columns
29-07-2020 23:21:01 - Loading data-03 file....
Loaded 300 rows and 5 columns
29-07-2020 23:21:01 - Loading data-04 file....
Loaded 300 rows and 5 columns
29-07-2020 23:21:02 - Loading data-05 file....
Loaded 300 rows and 5 columns
29-07-2020 23:21:02 - Loading data-06 file....
Loaded 149 rows and 5 columns
29-07-2020 23:21:03 - Loading data-07 file....
Loaded 242 rows and 5 columns
29-07-2020 23:21:08 - Loading data-08 file....
Loaded 177 rows and 5 columns
29-07-2020 23:21:09 - Loading data-09 file....
Loaded 206 rows and 5 columns
29-07-2020 23:21:10 - Loading data-10 file....
Loaded 247 rows and 5 columns
29-07-2020 23:21:11 - Loading data-11 file....
Loaded 236 rows and 5 columns
29-07-2020 23:21:12 - Loading data-12 file....
Loaded 300 rows and 5 columns
29-07-2020 23:21:12 - Loading data-13 file....
Loaded 300 rows and 5 columns

In [180]:
# Impute missing values for historical and prediction data
hist_data = functions.impute_na(hist_data)
# pred_data = functions.impute_na(pred_data)
# (analysis data already imputed missing values when the file was loaded)


29-07-2020 22:33:21 - Working with missing values...
Removing rows with more than 30% of missing data...
0 rows removed

Showing columns with missing values: 
                   count  density
race                2273     0.02
weight             98569     0.97
payer_code         40256     0.40
medical_specialty  49949     0.49
diag_1                21     0.00
diag_2               358     0.00
diag_3              1423     0.01

Removing rows with more than 30% of missing data (weight, payer_code, medical_specialty) ...

29-07-2020 22:34:49 - Columns removed. 
New shape: (101766 rows x 47 columns)

29-07-2020 22:34:51 - Replacing missing values...
Replacing NAs values of attribute race by value Caucasian
Replacing NAs values of attribute diag_1 by value 428
Replacing NAs values of attribute diag_2 by value 276
Replacing NAs values of attribute diag_3 by value 250

29-07-2020 22:35:26 - Missing values removed.  This operation has taken 124.96 s


In [181]:
hist_data = hist_data.withColumn("encounter_id",hist_data["encounter_id"].cast(StringType())) \
                    .withColumn("discharge_disposition_id",hist_data["discharge_disposition_id"].cast(StringType())) \
                    .withColumn("admission_source_id",hist_data["admission_source_id"].cast(StringType())) \
                    .withColumn("admission_type_id",hist_data["admission_type_id"].cast(StringType())) \
                    .withColumn("patient_nbr",hist_data["patient_nbr"].cast(StringType()))

hist_data.printSchema()
# pred_data.printSchema()
# an_data.printSchema()

root
 |-- encounter_id: string (nullable = true)
 |-- patient_nbr: string (nullable = true)
 |-- race: string (nullable = false)
 |-- gender: string (nullable = true)
 |-- age: string (nullable = true)
 |-- admission_type_id: string (nullable = true)
 |-- discharge_disposition_id: string (nullable = true)
 |-- admission_source_id: string (nullable = true)
 |-- time_in_hospital: integer (nullable = true)
 |-- num_lab_procedures: integer (nullable = true)
 |-- num_procedures: integer (nullable = true)
 |-- num_medications: integer (nullable = true)
 |-- number_outpatient: integer (nullable = true)
 |-- number_emergency: integer (nullable = true)
 |-- number_inpatient: integer (nullable = true)
 |-- diag_1: string (nullable = false)
 |-- diag_2: string (nullable = false)
 |-- diag_3: string (nullable = false)
 |-- number_diagnoses: integer (nullable = true)
 |-- max_glu_serum: string (nullable = true)
 |-- A1Cresult: string (nullable = true)
 |-- metformin: string (nullable = true)
 |-- r

### Analyze, preprocess and predict the data

#### Historical data

In [169]:
#drop unnecessary columns
columns_to_drop = ['encounter_id', 'race', 'age', 'payer_code', 'medical_specialty']
hist_data_aux = hist_data.drop(*columns_to_drop)

hist_data_aux = hist_data_aux.select(['metformin', 'repaglinide', 'nateglinide', 'chlorpropamide', 'glimepiride', 'acetohexamide', 
                                 'glipizide', 'glyburide', 'tolbutamide', 'pioglitazone', 'rosiglitazone', 'acarbose', 
                                  'miglitol', 'troglitazone', 'tolazamide', 'examide', 'citoglipton', 'insulin', 'glyburide-metformin',
                                 'glipizide-metformin', 'glimepiride-pioglitazone', 'readmitted'])

In [170]:
readmitted_mapping = {"<30": 0, ">30" : 0, "NO": 1}
mapping_expr = create_map([lit(x) for x in chain(*readmitted_mapping.items())])
hist_data_aux = hist_data_aux.withColumn("readmitted", mapping_expr.getItem(col("readmitted")))

In [8]:
## count number of categories of each categorical variable
from collections import defaultdict
from pyspark.sql.functions import countDistinct, approxCountDistinct

data_types = defaultdict(list)
for entry in hist_data_aux.schema.fields:
     data_types[str(entry.dataType)].append(entry.name)

counts_summary = hist_data_aux.agg(*[countDistinct(c).alias(c) for c in data_types["StringType"]])
counts_summary = counts_summary.toPandas()

counts = pd.Series(counts_summary.values.ravel())
counts.index = counts_summary.columns

sorted_vars = counts.sort_values(ascending = False) # number of categories of each variable
ignore = list((sorted_vars[sorted_vars <=1]).index) # variables with less than 1 category
# We'll ignore the categorical variables with only 1 category

from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoder, StringIndexer
        
strings_used = [var for var in data_types["StringType"] if var not in ignore]
stage_string = [StringIndexer(inputCol= c, outputCol= c+"_string_encoded") for c in strings_used]
stage_one_hot = [OneHotEncoder(inputCol= c+"_string_encoded", outputCol= c+ "_one_hot") for c in strings_used]

ppl = Pipeline(stages= stage_string + stage_one_hot)
hist_data_trunc = ppl.fit(hist_data_aux).transform(hist_data_aux)

features = data_types["IntegerType"] + [var + "_one_hot" for var in strings_used]
hist_data_trunc = VectorAssembler(inputCols = [x for x in features if x not in 'readmitted'], outputCol= "features")\
                .transform(hist_data_trunc).select(['readmitted', 'features'])

In [17]:
## Split data into train, validation and test
train_histC_trunc, test_hist_trunc = functions.df_split(hist_data_trunc, 0.7)
train_hist_trunc, val_hist_trunc = functions.df_split(train_histC_trunc, 0.7)

## Split data into X and Y coordinates
train_hist_trunc, val_hist_trunc =  functions.df_split(train_histC_trunc, 0.7)

print("train_hist: {0} x {1}\t val_hist: {2} x {3}\t test_hist: {4} x {5}"\
      .format(train_hist_trunc.count(), len(train_hist_trunc.columns),
              val_hist_trunc.count(), len(val_hist_trunc.columns),
              test_hist_trunc.count(), len(test_hist_trunc.columns)))

train_hist: 49690 x 2	 val_hist: 21370 x 2	 test_hist: 30706 x 2


In [23]:
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.evaluation import BinaryClassificationEvaluator

lr = LogisticRegression(maxIter=1000, regParam=0, elasticNetParam=0.8, featuresCol="features", labelCol="readmitted")
model = lr.fit(train_hist_trunc)

evaluator = BinaryClassificationEvaluator(labelCol='readmitted')

y_train_hist = model.transform(train_hist_trunc)
train_accuracy = evaluator.evaluate(y_train_hist)
print("Training accuracy: {:.2f}".format(train_accuracy))

y_val_hist = model.transform(val_hist_trunc)
val_accuracy = evaluator.evaluate(y_val_hist)
print("Validation accuracy: {:.2f}".format(val_accuracy))

y_test = model.transform(test_hist_trunc)
test_accuracy = evaluator.evaluate(y_test)
print("Test accuracy: {:.2f}".format(test_accuracy))

Training accuracy: 0.55
Validation accuracy: 0.55
Test accuracy: 0.55


In [182]:
import pyspark.sql.functions as f
hist_data = hist_data.withColumn("diag_1", f.translate(f.col("diag_1"), ".", "")) \
               .withColumn("diag_2", f.translate(f.col("diag_2"), ".", "")) \
               .withColumn("diag_3", f.translate(f.col("diag_3"), ".", ""))

In [183]:
hist_data.select(["diag_1", "diag_2", "diag_3"]).show()

+------+------+------+
|diag_1|diag_2|diag_3|
+------+------+------+
| 25083|   276|   250|
|   276| 25001|   255|
|   648|   250|   V27|
|     8| 25043|   403|
|   197|   157|   250|
|   414|   411|   250|
|   414|   411|   V45|
|   428|   492|   250|
|   398|   427|    38|
|   434|   198|   486|
|  2507|   403|   996|
|   157|   288|   197|
|   428| 25043|  2506|
|   428|   411|   427|
|   518|   998|   627|
|   999|   507|   996|
|   410|   411|   414|
|   682|   174|   250|
|   402|   425|   416|
|   737|   427|   714|
+------+------+------+
only showing top 20 rows



In [202]:
admission_type_id_mapping = {'1': 'Emergency','2':'Urgent', '3':'Elective', '4':'Newborn', '5':'Not Available', 
                             '6':'NULL', '7':'Trauma Center', '8':'Not Mapped'}
discharge_disposition_id_mapping = {
    '1':'Discharged to home',
    '2':'Discharged/transferred to another short term hospital',
    '3':'Discharged/transferred to SNF',
    '4':'Discharged/transferred to ICF',
    '5':'Discharged/transferred to another type of inpatient care institution',
    '6':'Discharged/transferred to home with home health service',
    '7':'Left AMA',
    '8':'Discharged/transferred to home under care of Home IV provider',
    '9':'Admitted as an inpatient to this hospital',
    '10':'Neonate discharged to another hospital for neonatal aftercare',
    '11':'Expired',
    '12':'Still patient or expected to return for outpatient services',
    '13':'Hospice / home',
    '14':'Hospice / medical facility',
    '15':'Discharged/transferred within this institution to Medicare approved swing bed',
    '16':'Discharged/transferred/referred another institution for outpatient services',
    '17':'Discharged/transferred/referred to this institution for outpatient services',
    '18':'NULL',
    '19':'Expired at home. Medicaid only, hospice.',
    '20':"Expired in a medical facility. Medicaid only, hospice.",
    '21':"Expired, place unknown. Medicaid only, hospice.",
    '22':'Discharged/transferred to another rehab fac including rehab units of a hospital.',
    '23':'Discharged/transferred to a long term care hospital.',
    '24':'Discharged/transferred to a nursing facility certified under Medicaid but not certified under Medicare.',
    '25':'Not Mapped',
    '26':'Unknown/Invalid',
    '30':'Discharged/transferred to another Type of Health Care Institution not Defined Elsewhere',
    '27':'Discharged/transferred to a federal health care facility.',
    '28':'Discharged/transferred/referred to a psychiatric hospital of psychiatric distinct part unit of a hospital',
    '29':'Discharged/transferred to a Critical Access Hospital (CAH).'
    }
admission_source_id_mapping = {
    '1':'Physician Referral',
    '2':'Clinic Referral',
    '3':'HMO Referral',
    '4':'Transfer from a hospital',
    '5':'Transfer from a Skilled Nursing Facility (SNF)',
    '6':'Transfer from another health care facility',
    '7':'Emergency Room',
    '8':'Court/Law Enforcement',
    '9':'Not Available',
    '10':'Transfer from critial access hospital',
    '11':'Normal Delivery',
    '12':'Premature Delivery',
    '13':'Sick Baby',
    '14':'Extramural Birth',
    '15':'Not Available',
    '17':'NULL',
    '18':'Transfer From Another Home Health Agency',
    '19':'Readmission to Same Home Health Agency',
    '20':'Not Mapped',
    '21':'Unknown/Invalid',
    '22':'Transfer from hospital inpt/same fac reslt in a sep claim',
    '23':'Born inside this hospital',
    '24':'Born outside this hospital',
    '25':'Transfer from Ambulatory Surgery Center',
    '26':'Transfer from Hospice'
    }

meds_mapping = {'Up': 1, 'Down': 2, 'Steady': 3, 'No': 4}

change_mapping = {"No": 0, "Ch" : 1}
diabetesMed_mapping = {"No": 0, "Yes" : 1}
readmitted_trunc_mapping = {"<30": 0, ">30" : 0, "NO": 1}

df = ss.read.load("tfm-marta/data/CMS30_DESC_LONG_DX.csv", format="csv", sep=";", inferSchema=True)
diag_mapping = df.toPandas().set_index('_c0').to_dict()['_c1']
diag_mapping


mapping_expr = create_map([lit(x) for x in chain(*admission_type_id_mapping.items())])
hist_data = hist_data.withColumn("admission_type_id", mapping_expr.getItem(col("admission_type_id")))

mapping_expr = create_map([lit(x) for x in chain(*discharge_disposition_id_mapping.items())])
hist_data = hist_data.withColumn("discharge_disposition_id", mapping_expr.getItem(col("discharge_disposition_id")))

mapping_expr = create_map([lit(x) for x in chain(*admission_source_id_mapping.items())])
hist_data = hist_data.withColumn("admission_source_id", mapping_expr.getItem(col("admission_source_id")))

mapping_expr = create_map([lit(x) for x in chain(*meds_mapping.items())])
hist_data = hist_data.withColumn("metformin", mapping_expr.getItem(col("metformin"))) \
                    .withColumn("repaglinide", mapping_expr.getItem(col("repaglinide"))) \
                    .withColumn("nateglinide", mapping_expr.getItem(col("nateglinide"))) \
                    .withColumn("chlorpropamide", mapping_expr.getItem(col("chlorpropamide"))) \
                    .withColumn("glimepiride", mapping_expr.getItem(col("glimepiride"))) \
                    .withColumn("acetohexamide", mapping_expr.getItem(col("acetohexamide"))) \
                    .withColumn("glipizide", mapping_expr.getItem(col("glipizide"))) \
                    .withColumn("glyburide", mapping_expr.getItem(col("glyburide"))) \
                    .withColumn("tolbutamide", mapping_expr.getItem(col("tolbutamide"))) \
                    .withColumn("pioglitazone", mapping_expr.getItem(col("pioglitazone"))) \
                    .withColumn("rosiglitazone", mapping_expr.getItem(col("rosiglitazone"))) \
                    .withColumn("acarbose", mapping_expr.getItem(col("acarbose"))) \
                    .withColumn("miglitol", mapping_expr.getItem(col("miglitol"))) \
                    .withColumn("troglitazone", mapping_expr.getItem(col("troglitazone"))) \
                    .withColumn("tolazamide", mapping_expr.getItem(col("tolazamide"))) \
                    .withColumn("examide", mapping_expr.getItem(col("examide"))) \
                    .withColumn("citoglipton", mapping_expr.getItem(col("citoglipton"))) \
                    .withColumn("insulin", mapping_expr.getItem(col("insulin"))) \
                    .withColumn("glyburide-metformin", mapping_expr.getItem(col("glyburide-metformin"))) \
                    .withColumn("glipizide-metformin", mapping_expr.getItem(col("glipizide-metformin"))) \
                    .withColumn("glimepiride-pioglitazone", mapping_expr.getItem(col("glimepiride-pioglitazone"))) \
                    .withColumn("metformin-rosiglitazone", mapping_expr.getItem(col("metformin-rosiglitazone"))) \
                    .withColumn("metformin-pioglitazone", mapping_expr.getItem(col("metformin-pioglitazone")))

mapping_expr = create_map([lit(x) for x in chain(*change_mapping.items())])
hist_data = hist_data.withColumn("change", mapping_expr.getItem(col("change")))

mapping_expr = create_map([lit(x) for x in chain(*diabetesMed_mapping.items())])
hist_data = hist_data.withColumn("diabetesMed", mapping_expr.getItem(col("diabetesMed")))

mapping_expr = create_map([lit(x) for x in chain(*readmitted_mapping.items())])
hist_data = hist_data.withColumn("readmitted", mapping_expr.getItem(col("readmitted"))) \
                        .withColumnRenamed("readmitted", "readmitted_trunc")

mapping_expr = create_map([lit(x) for x in chain(*diag_mapping.items())])
hist_data = hist_data.withColumn("diag_1", mapping_expr.getItem(col("diag_1"))) \
                     .withColumn("diag_2", mapping_expr.getItem(col("diag_2"))) \
                     .withColumn("diag_3", mapping_expr.getItem(col("diag_3")))

hist_data = hist_data.withColumn("Accuracy", lit(test_accuracy))
from datetime import date
hist_data = hist_data.withColumn("date", lit(date.today()))

hist_data.printSchema()

root
 |-- encounter_id: string (nullable = true)
 |-- patient_nbr: string (nullable = true)
 |-- race: string (nullable = false)
 |-- gender: string (nullable = true)
 |-- age: string (nullable = true)
 |-- admission_type_id: string (nullable = true)
 |-- discharge_disposition_id: string (nullable = true)
 |-- admission_source_id: string (nullable = true)
 |-- time_in_hospital: integer (nullable = true)
 |-- num_lab_procedures: integer (nullable = true)
 |-- num_procedures: integer (nullable = true)
 |-- num_medications: integer (nullable = true)
 |-- number_outpatient: integer (nullable = true)
 |-- number_emergency: integer (nullable = true)
 |-- number_inpatient: integer (nullable = true)
 |-- diag_1: string (nullable = true)
 |-- diag_2: string (nullable = true)
 |-- diag_3: string (nullable = true)
 |-- number_diagnoses: integer (nullable = true)
 |-- max_glu_serum: string (nullable = true)
 |-- A1Cresult: string (nullable = true)
 |-- metformin: integer (nullable = true)
 |-- rep

#### Prediction data

blablablablabla

In [ ]:
## Split data into train, validation and test
train_predC, test_pred = functions.df_split(pred_data, 0.7)
train_pred, val_pred = functions.df_split(train_predC, 0.7)

## Split data into X and Y coordinates
Xtrain_pred, ytrain_pred = train_pred.select(train_pred.columns[0:len(train_pred.columns)-1]), train_pred.select('Class')
Xval_pred, yval_pred =  val_pred.select(val_pred.columns[0:len(val_pred.columns)-1]), val_pred.select('Class')
Xtest_pred, ytest_pred = test_pred.select(test_pred.columns[0:len(test_pred.columns)-1]), test_pred.select('Class')

print("Xtrain_pred: {0} x {1}\t ytrain_pred: {2} x {3}".format(Xtrain_pred.count(), len(Xtrain_pred.columns),
                                                              ytrain_pred.count(), len(ytrain_pred.columns)))
print("Xval_pred: {0} x {1}\t yval_pred: {2} x {3}".format(Xval_pred.count(), len(Xval_pred.columns),
                                                              yval_pred.count(), len(yval_pred.columns)))
print("Xtest_pred: {0} x {1}\t ytest_pred: {2} x {3}".format(Xtest_pred.count(), len(Xtest_pred.columns),
                                                              ytest_pred.count(), len(ytest_pred.columns)))

In [ ]:
# Put together all the input attributes.
assembler = VectorAssembler(inputCols=[x for x in train_predC.columns if x not in 'Class'], outputCol='features')

train_predC_trunc = assembler.transform(train_predC).select(['Class', 'features'])
train_pred_trunc = assembler.transform(train_pred).select(['Class', 'features'])
val_pred_trunc = assembler.transform(val_pred).select(['Class', 'features'])
test_pred_trunc = assembler.transform(test_pred).select(['Class', 'features'])
print(train_pred_trunc.show(3))

In [ ]:
from pyspark.ml.classification import LinearSVC
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import BinaryClassificationEvaluator

model = LinearSVC(labelCol='Class')
paramGrid = ParamGridBuilder() \
        .addGrid(model.regParam, [1.0, 0.1, 0.01, 0.001, 0.0001, 0.0]) \
        .build()
evaluator = BinaryClassificationEvaluator(labelCol='Class')
crossval = CrossValidator(estimator=model, estimatorParamMaps=paramGrid, evaluator=evaluator, parallelism=2, numFolds=5)

# Run cross-validation, and choose the best set of parameters.
cvModel = crossval.fit(train_pred_trunc)
print("Regularization parameter: {}".format(cvModel.bestModel._java_obj.getRegParam()))

y_train_pred = cvModel.transform(train_pred_trunc)
train_accuracy = evaluator.evaluate(y_train_pred)
print("Training accuracy: {:.2f}".format(train_accuracy))

y_val_pred = cvModel.transform(val_pred_trunc)
val_accuracy = evaluator.evaluate(y_val_pred)
print("Validation accuracy: {:.2f}".format(val_accuracy))

### Final model
model = LinearSVC(labelCol='Class', regParam=cvModel.bestModel._java_obj.getRegParam()).fit(train_predC_trunc)
y_test = model.transform(test_pred_trunc)
test_accuracy = evaluator.evaluate(y_test)
print("Test accuracy: {:.2f}".format(test_accuracy))

In [ ]:
pred_data = pred_data.withColumn("Accuracy", lit(test_accuracy))
pred_data = pred_data.withColumn("new_column",lit("ABC"))
w = Window().partitionBy('new_column').orderBy(lit('A'))
pred_data = pred_data.withColumn("patient_nbr", 50125+row_number().over(w)).drop("new_column")
pred_data = pred_data.withColumn("patient_nbr",pred_data["patient_nbr"].cast(StringType()))

pred_data.show()

#### Analysis data

blablablablabla

In [215]:
an_data = an_data.withColumn("value",an_data["value"].cast(IntegerType())) 

mapping = {
    '33' : 'Regular insulin dose',
    '34' : 'NPH insulin dose',
    '35' : 'UltraLente insulin dose',
    '48' : 'Unspecified blood glucose measurement',
    '57' : 'Unspecified blood glucose measurement',
    '58' : 'Pre-breakfast blood glucose measurement',
    '59' : 'Post-breakfast blood glucose measurement',
    '60' : 'Pre-lunch blood glucose measurement',
    '61' : 'Post-lunch blood glucose measurement',
    '62' : 'Pre-supper blood glucose measurement',
    '63' : 'Post-supper blood glucose measurement',
    '64' : 'Pre-snack blood glucose measurement',
    '65' : 'Hypoglycemic symptoms',
    '66' : 'Typical meal ingestion',
    '67' : 'More-than-usual meal ingestion',
    '68' : 'Less-than-usual meal ingestion',
    '69' : 'Typical exercise activity',
    '70' : 'More-than-usual exercise activity',
    '71' : 'Less-than-usual exercise activity',
    '72' : 'Unspecified special event'}

mapping_expr = create_map([lit(x) for x in chain(*mapping.items())])
an_data = an_data.withColumn("code", mapping_expr.getItem(col("code"))) \
                 .withColumn("patient_nbr",an_data["patient_nbr"].cast(StringType())) \
                 .withColumn('date', an_data.date + f.expr('INTERVAL 29 years'))
an_data.printSchema()
an_data.show()

root
 |-- code: string (nullable = true)
 |-- value: integer (nullable = true)
 |-- patient_nbr: string (nullable = false)
 |-- date: timestamp (nullable = true)

+--------------------+-----+-----------+-------------------+
|                code|value|patient_nbr|               date|
+--------------------+-----+-----------+-------------------+
|Pre-breakfast blo...|  100|      70126|2020-04-21 09:09:00|
|Regular insulin dose|    9|      70126|2020-04-21 09:09:00|
|    NPH insulin dose|   13|      70126|2020-04-21 09:09:00|
|Pre-supper blood ...|  119|      70126|2020-04-21 17:08:00|
|Regular insulin dose|    7|      70126|2020-04-21 17:08:00|
|Unspecified blood...|  123|      70126|2020-04-21 22:51:00|
|Pre-breakfast blo...|  216|      70126|2020-04-22 07:35:00|
|Regular insulin dose|   10|      70126|2020-04-22 07:35:00|
|    NPH insulin dose|   13|      70126|2020-04-22 07:35:00|
|Regular insulin dose|    2|      70126|2020-04-22 13:40:00|
|Pre-supper blood ...|  211|      70126|2020

## Indexing data into elasticsearch

In [199]:
from elasticsearch import Elasticsearch # Import Elasticsearch package 

myHost = "192.168.146.131"

es = Elasticsearch([{"host": myHost,"port":9200}]) # Connect to the elastic cluster
print(es)

def uploadToES(indexName, indexBody, docType=None, requestBody=None, verbose=True):
    if (es.indices.exists(indexName)==False): 
        es.indices.create(index=indexName, body=requestBody)
        if(verbose): print("creating {} index...".format(indexName))
    es.index(index=indexName,doc_type=docType, body=indexBody) # Store the document in Elasticsearch
    if(verbose): print("adding document {} to {} index...".format(indexBody, indexName))

<Elasticsearch([{'host': '192.168.146.131', 'port': 9200}])>


In [216]:
data_requestBody = {
    "settings" : {
        "number_of_shards": 1,
        "number_of_replicas": 1
    },
    "mappings": {
        "properties": {
            "encounter_id": {"type": "text"},
            "patient_nbr": {"type": "text"},
            "race": {"type": "text"},
            "gender":{"type": "text"},
            "age":{"type":"text"},
            "admission_type_id":{"type":"text"},
            "discharge_disposition_id":{"type":"text"},
            "admission_source_id":{"type":"text"},
            "time_in_hospital":{"type":"integer"},
            "num_lab_procedures":{"type":"integer"},
            "num_procedures":{"type":"integer"},
            "num_medications":{"type":"integer"},
            "number_outpatient":{"type":"integer"},
            "number_emergency":{"type":"integer"},
            "number_inpatient":{"type":"integer"},
            "diag_1":{"type":"text"},
            "diag_2":{"type":"text"},
            "diag_3":{"type":"text"},
            "number_diagnoses":{"type":"integer"},
            "max_glu_serum":{"type":"text"},
            "A1Cresult":{"type":"text"},
            "metformin":{"type":"integer"},
            "repaglinide":{"type":"integer"},
            "nateglinide":{"type":"integer"},
            "chlorpropamide":{"type":"integer"},
            "glimepiride":{"type":"integer"},
            "acetohexamide":{"type":"integer"},
            "glipizide":{"type":"integer"},
            "glyburide":{"type":"integer"},
            "tolbutamide":{"type":"integer"},
            "pioglitazone":{"type":"integer"},
            "rosiglitazone":{"type":"integer"},
            "acarbose":{"type":"integer"},
            "miglitol":{"type":"integer"},
            "troglitazone":{"type":"integer"},
            "tolazamide":{"type":"integer"},
            "examide":{"type":"integer"},
            "citoglipton":{"type":"integer"},
            "insulin":{"type":"integer"},
            "glyburide-metformin":{"type":"integer"},
            "glipizide-metformin":{"type":"integer"},
            "glimepiride-pioglitazone":{"type":"integer"},
            "metformin-rosiglitazone":{"type":"integer"},
            "metformin-pioglitazone":{"type":"integer"},
            "change":{"type":"integer"},
            "diabetesMed":{"type":"integer"},
            "readmitted_trunc ":{"type":"integer"},
            "Accuracy":{"type":"double"}
        }
    }
}
# aux=hist_data.limit(200).toPandas()
# for i in range(0, aux.shape[0]):
#     body=aux.iloc[i].to_json(orient="index")
#     uploadToES("tfm-marta-historical-data", body)
# aux=pred_data.toPandas()
# for i in range(0, aux.shape[0]):
#     body=aux.iloc[i].to_json(orient="index")
#     uploadToES("tfm-marta-prediction-data", body, docType='document')
    
# an_requestBody = {
#     "mappings": {
#         "properties": {
#             "date": {"type": "date", "format":"yyyy-MM-dd HH:mm || yyyy-MM-dd || epoch_millis", "ignore_malformed":True},
#             "code": {"type": "keyword"},
#             "value":{"type": "long"}
#         }
#     }
# # }

aux=an_data.toPandas()    
for j in range(0, aux.shape[0]):   
    body=aux.iloc[j].to_json(orient="index", date_format='iso')
    uploadToES("tfm-marta-analysis-data", body)

creating tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measurement","value":100.0,"patient_nbr":"70126","date":"2020-04-21T09:09:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":9.0,"patient_nbr":"70126","date":"2020-04-21T09:09:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":13.0,"patient_nbr":"70126","date":"2020-04-21T09:09:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-supper blood glucose measurement","value":119.0,"patient_nbr":"70126","date":"2020-04-21T17:08:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":7.0,"patient_nbr":"70126","date":"2020-04-21T17:08:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Unspecified blood glucose measurement","value":123.0,"patient_nbr":"70126","date":"2020-04-21T22:51:00.000Z"} to tfm-marta-analysis-data 

adding document {"code":"Pre-supper blood glucose measurement","value":263.0,"patient_nbr":"70126","date":"2020-04-29T16:50:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":8.0,"patient_nbr":"70126","date":"2020-04-29T16:50:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Unspecified blood glucose measurement","value":81.0,"patient_nbr":"70126","date":"2020-04-29T22:28:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measurement","value":179.0,"patient_nbr":"70126","date":"2020-04-30T07:40:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":10.0,"patient_nbr":"70126","date":"2020-04-30T07:40:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":14.0,"patient_nbr":"70126","date":"2020-04-30T07:40:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-lunc

adding document {"code":"Pre-supper blood glucose measurement","value":229.0,"patient_nbr":"70126","date":"2020-05-06T16:55:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":7.0,"patient_nbr":"70126","date":"2020-05-06T16:55:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measurement","value":121.0,"patient_nbr":"70126","date":"2020-05-07T07:37:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":10.0,"patient_nbr":"70126","date":"2020-05-07T07:37:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":14.0,"patient_nbr":"70126","date":"2020-05-07T07:37:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":5.0,"patient_nbr":"70126","date":"2020-05-07T12:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","val

adding document {"code":"Regular insulin dose","value":7.0,"patient_nbr":"70126","date":"2020-05-16T17:41:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Unspecified blood glucose measurement","value":69.0,"patient_nbr":"70126","date":"2020-05-16T22:41:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measurement","value":76.0,"patient_nbr":"70126","date":"2020-05-17T07:35:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":9.0,"patient_nbr":"70126","date":"2020-05-17T07:35:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":14.0,"patient_nbr":"70126","date":"2020-05-17T07:35:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":5.0,"patient_nbr":"70126","date":"2020-05-17T12:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-supper blood glucose mea

adding document {"code":"Unspecified blood glucose measurement","value":180.0,"patient_nbr":"70126","date":"2020-05-26T22:06:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":2.0,"patient_nbr":"70126","date":"2020-05-26T22:06:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measurement","value":295.0,"patient_nbr":"70126","date":"2020-05-27T08:50:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":11.0,"patient_nbr":"70126","date":"2020-05-27T08:50:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":15.0,"patient_nbr":"70126","date":"2020-05-27T08:50:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-lunch blood glucose measurement","value":220.0,"patient_nbr":"70126","date":"2020-05-27T13:48:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular 

...

adding document {"code":"NPH insulin dose","value":7.0,"patient_nbr":"70195","date":"2018-03-31T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":1.0,"patient_nbr":"70195","date":"2018-04-01T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":8.0,"patient_nbr":"70195","date":"2018-04-01T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-supper blood glucose measurement","value":361.0,"patient_nbr":"70195","date":"2018-04-01T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":2.0,"patient_nbr":"70195","date":"2018-04-01T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":7.0,"patient_nbr":"70195","date":"2018-04-01T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Unspecified blood glucose measurement","value":127.0,"pat

adding document {"code":"NPH insulin dose","value":8.0,"patient_nbr":"70195","date":"2018-04-10T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-supper blood glucose measurement","value":356.0,"patient_nbr":"70195","date":"2018-04-10T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":2.0,"patient_nbr":"70195","date":"2018-04-10T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":7.0,"patient_nbr":"70195","date":"2018-04-10T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measurement","value":171.0,"patient_nbr":"70195","date":"2018-04-11T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":1.0,"patient_nbr":"70195","date":"2018-04-11T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":8.0,"p

adding document {"code":"Regular insulin dose","value":2.0,"patient_nbr":"70195","date":"2018-04-20T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":8.0,"patient_nbr":"70195","date":"2018-04-20T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-supper blood glucose measurement","value":223.0,"patient_nbr":"70195","date":"2018-04-20T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":1.0,"patient_nbr":"70195","date":"2018-04-20T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":7.0,"patient_nbr":"70195","date":"2018-04-20T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":1.0,"patient_nbr":"70195","date":"2018-04-21T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":8.0,"patient_nbr":"70195","

adding document {"code":"Regular insulin dose","value":1.0,"patient_nbr":"70195","date":"2018-04-30T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":7.0,"patient_nbr":"70195","date":"2018-04-30T08:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-lunch blood glucose measurement","value":246.0,"patient_nbr":"70195","date":"2018-04-30T12:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Regular insulin dose","value":1.0,"patient_nbr":"70195","date":"2018-04-30T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"NPH insulin dose","value":6.0,"patient_nbr":"70195","date":"2018-04-30T18:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Unspecified blood glucose measurement","value":202.0,"patient_nbr":"70195","date":"2018-04-30T22:00:00.000Z"} to tfm-marta-analysis-data index...
adding document {"code":"Pre-breakfast blood glucose measure

adding document {"code":"NPH insulin dose","value":7.0,"patient_nbr":"70195","date":"2018-05-12T08:00:00.000Z"} to tfm-marta-analysis-data index...


In [ ]:
# Code to read data form Elasticsearch
'''from pyspark import SparkConf, SparkContext
from pyspark.sql import SQLContext
import os

os.environ['PYSPARK_SUBMIT_ARGS']='--jars /usr/local/spark/jars/elasticsearch-hadoop-7.6.2.jar pyspark-shell'
sc = SparkContext(appName="ESTest")
sqlContext = SQLContext(sc)
es_read_conf = {
    "es.nodes" : '192.168.146.131',        
    "es.port" : '9200',
    "es.resource" : "tfm-marta-analysis-data01"
}

es_rdd = sc.newAPIHadoopRDD(
    inputFormatClass="org.elasticsearch.hadoop.mr.EsInputFormat",
    keyClass="org.apache.hadoop.io.NullWritable",
    valueClass="org.elasticsearch.hadoop.mr.LinkedMapWritable",
    conf=es_read_conf)

print(sqlContext.createDataFrame(es_rdd).collect())
sc.stop()'''

In [ ]:
data_requestBody = {
    "settings" : {
        "number_of_shards": 2,
        "number_of_replicas": 1
    },
    "mappings": {
        "properties": {
            "encounter_id": {"type": "keyword"},
            "patient_nbr": {"type": "keyword"},
            "race": {"type": "text"},
            "gender":{"type": "text"},
#             "age":{"type":"integer"},
            "admission_type_id":{"type":"keyword"},
            "discharge_disposition_id":{"type":"keyword"},
            "admission_source_id":{"type":"keyword"},
            "time_in_hospital":{"type":"integer"},
            "num_lab_procedures":{"type":"integer"},
            "num_procedures":{"type":"integer"},
            "num_medications":{"type":"integer"},
            "number_outpatient":{"type":"integer"},
            "number_emergency":{"type":"integer"},
            "number_inpatient":{"type":"integer"},
            "diag_1":{"type":"keyword"},
            "diag_2":{"type":"keyword"},
            "diag_3":{"type":"keyword"},
            "number_diagnoses":{"type":"integer"},
            "max_glu_serum":{"type":"text"},
            "A1Cresult":{"type":"text"},
            "medications":[{
                "metformin":{"type":"inte"},
                "repaglinide":{"type":"text"},
                "nateglinide":{"type":"text"},
                "chlorpropamide":{"type":"text"},
                "glimepiride":{"type":"text"},
                "acetohexamide":{"type":"text"},
                "glipizide":{"type":"text"},
                "glyburide":{"type":"text"},
                "tolbutamide":{"type":"text"},
                "pioglitazone":{"type":"text"},
                "rosiglitazone":{"type":"text"},
                "acarbose":{"type":"text"},
                "miglitol":{"type":"text"},
                "troglitazone":{"type":"text"},
                "tolazamide":{"type":"text"},
                "examide":{"type":"text"},
                "citoglipton":{"type":"text"},
                "insulin":{"type":"text"},
                "glyburide-metformin":{"type":"text"},
                "glipizide-metformin":{"type":"text"},
                "glimepiride-pioglitazone":{"type":"text"},
                "metformin-rosiglitazone":{"type":"text"},
                "metformin-pioglitazone":{"type":"text"},
                }]
            "change":{"type":"text"},
            "diabetesMed":{"type":"text"},
            "readmitted ":{"type":"text"},
# probability of readmission
            
            "pregnancies":{"type":"integer"},
            "glucose":{"type":"integer"},
            "blood_pressure":{"type":"integer"},
            "skin_thickness":{"type":"integer"},
            "insulin":{"type":"integer"},
            "outcome":{"type":"integer"},
#             "accuracy":0.93,
            "age": {"type":"integer"},
            "bmi": {"type":"double"},
            "diabetes-predigree-function":{"type":"double"},

            "monitoring": [{
                "date": {"type": "date", "format":"yyyy-MM-dd HH:mm || yyyy-MM-dd || epoch_millis", "ignore_malformed":True},
                "code": {"type": "keyword"},
                "value":{"type": "long"}
            }]
        }
    }
}